![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS - módulo O 2019 Acidentes

## Bibliotecas Utilizadas

In [ ]:
#Lendo pacotes necessários
library(survey)
library(dplyr)
library(tictoc)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [ ]:
#Carregando banco de dados
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA>")

## Definição do peso e filtragem de respondentes do questionário

In [3]:
#Selecionando registros válidos para o módulo U e calculando peso amostral - summary de verificação
pns2019.1<-pns2019v6 %>% filter(V0025A==1)
pns2019.1<-pns2019.1 %>% mutate(peso_morador_selec=((V00291*(94114/168426190))))
pns2019.1<-pns2019.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2019.1$peso_morador_selec)

    Min.  1st Qu.   Median     Mean  3rd Qu.     Max. 
 0.00582  0.27579  0.56358  1.03597  1.16822 63.29775 

## Criação de variáveis dos indicadores

In [4]:
#Usa sempre cinto quando anda no banco de trás de automóvel. - O002P
pns2019.1 <- pns2019.1  %>% mutate(O002P= ifelse(O00501==1,NA,ifelse(O00501==2,1,2) ))
pns2019.1$O002P<-factor(pns2019.1$O002P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$O002P)

#Usa sempre capacete quando dirige motocicleta. - O003P

pns2019.1 <- pns2019.1 %>% mutate(O003P= ifelse(O00701==1,1,2))
pns2019.1$O003P<-factor(pns2019.1$O003P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$O003P)

#Usa sempre capacete quando está como passageiro de motocicleta. - O004P

pns2019.1 <- pns2019.1 %>% mutate(O004P= ifelse(O00801==1,NA,ifelse(O00801==2,1,2)))
pns2019.1$O004P<-factor(pns2019.1$O004P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$O004P)

#Usa sempre capacete quando está como passageiro de motocicleta. - O005P
pns2019.1 <- pns2019.1  %>% mutate(O005P = ifelse(O00101==1 | O00201==1,2,2))  
pns2019.1 <- pns2019.1  %>% mutate(O005P = ifelse(O00802<=4,1,2))  
pns2019.1$O005P<-factor(pns2019.1$O005P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$O005P)

#Usa sempre capacete quando está como passageiro de motocicleta. - O006P
pns2019.1 <- pns2019.1  %>% mutate(O006P = ifelse(O009==1,1,
                                          ifelse(O009==2,2,2)))   
pns2019.1$O006P<-factor(pns2019.1$O006P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$O006P)

#Usa sempre cinto quando dirige. - O007P
pns2019.1 <- pns2019.1  %>% mutate(O007P = ifelse(O00401==1,1,
                                          ifelse(O00101==2,2,2)))   
pns2019.1$O007P<-factor(pns2019.1$O007P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$O007P)


#Usa sempre cinto quando anda na frente como passageiro. - O008P
pns2019.1 <- pns2019.1  %>% mutate(O008P = ifelse(O00402==2,1,
                                          ifelse(O00402>=2,2,2)))   
pns2019.1$O008P<-factor(pns2019.1$O008P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$O008P)

Sim   Não  NA's 
45832 38603  6411

Sim   Não  NA's 
17149  5254 68443

Sim   Não  NA's 
40636 15126 35084

Sim   Não  NA's 
11479 30406 48961

Sim   Não 
 2257 88589

Sim   Não  NA's 
26396  4973 59477

Sim   Não 
68537 22309

## Definições de abrangências

### Situação urbana ou rural

In [5]:
#Situação Urbano ou Rural
pns2019.1 <- pns2019.1 %>% rename(Sit_Urbano_Rural=V0026)
pns2019.1$Sit_Urbano_Rural<-factor(pns2019.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("urbano", "rural"))
summary(pns2019.1$Sit_Urbano_Rural)

urbano  rural 
 69873  20973

### Sexo

In [6]:
#Sexo
pns2019.1 <- pns2019.1 %>% rename(Sexo=C006)
pns2019.1$Sexo<-factor(pns2019.1$Sexo, levels=c(1,2), labels=c("Masculino", "Feminino"))
summary(pns2019.1$Sexo)

Masculino  Feminino 
    42799     48047

### UF

In [7]:
#Estados - UFs
pns2019.1 <- pns2019.1 %>% rename(Unidades_da_Federacao=V0001)
pns2019.1$Unidades_da_Federacao<-factor(pns2019.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2019.1$Unidades_da_Federacao)

Rondônia                Acre            Amazonas             Roraima 
               2176                2380                3479                2238 
               Pará               Amapá           Tocantins            Maranhão 
               3853                1554                1922                5080 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               2740                4265                2962                3158 
         Pernambuco             Alagoas             Sergipe               Bahia 
               4083                2987                2610                3659 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
               5209                3541                4966                6114 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3967                3738                3767                2863 
        Mato Grosso               Goiás    Distrito Federal 
               2468                2702                2365

### Grandes Regiões

In [8]:
#Grandes Regiões
pns2019.1 <- pns2019.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2019.1$GrandesRegioes)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       17602        31544        19830        11472        10398

### Faixa Etária

In [9]:
#Faixas Etárias
pns2019.1 <-  pns2019.1 %>% mutate(faixa_idade=cut(C008,
  breaks = c(18,30, 45, 60,Inf),
  labels = c("18 a 29 anos","30 a 44 anos","45 a 59 anos","60 anos ou mais"), 
  ordered_result = TRUE, right = FALSE))
summary(pns2019.1$faixa_idade) 

18 a 29 anos    30 a 44 anos    45 a 59 anos 60 anos ou mais            NA's 
          15394           26754           23655           22728            2315

### Raça

In [10]:
#Raça
pns2019.1 <- pns2019.1 %>% mutate(Raca= ifelse(C009==1, 1, 
                        ifelse(C009==2, 2, 
                            ifelse(C009==4, 3, 9))))
pns2019.1$Raca<-factor(pns2019.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))
summary(pns2019.1$Raca)

Branca  Preta  Parda   NA's 
 33133  10345  45994   1374

### Renda per capita

In [11]:
#Rendimento domiciliar per capita
pns2019.1 <- pns2019.1 %>% mutate(rend_per_capita = ifelse(VDF004 %in% 1:2, 1, 
                        ifelse(VDF004%in% 3, 2, 
                        ifelse(VDF004%in% 4, 3,
                        ifelse(VDF004%in% 5, 4,5)))))

pns2019.1$rend_per_capita<-factor(pns2019.1$rend_per_capita, levels=c(1,2,3,4,5), labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM",
                                                                                   "2 até 3 SM","Mais de 3 SM"))
summary(pns2019.1$rend_per_capita)


Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM 
       23697        26406        22466         7612        10665

### Escolaridade

In [12]:
# Escolaridade
pns2019.1 <- pns2019.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))

pns2019.1$gescol<-factor(pns2019.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Fundamental incompleto ou equivalente","Médio incompleto ou equivalente",
                                           "Superior incompleto ou equivalente","Superior completo"))
summary(pns2019.1$gescol)

Fundamental incompleto ou equivalente       Médio incompleto ou equivalente 
                                36276                                 13520 
   Superior incompleto ou equivalente                     Superior completo 
                                27433                                 13617

### Capital

In [13]:
#Capital
pns2019.1<- pns2019.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2019.1$Capital)

Porto Velho     Rio Branco         Manaus      Boa Vista          Belém 
          2176           2380           3479           2238           3853 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          1554           1922           5080           2740           4265 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          2962           3158           4083           2987           2610 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
          3659           5209           3541           4966           6114 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
          3967           3738           3767           2863           2468 
       Goiânia       Brasília 
          2702           2365

## Criando indicadores

### Filtrando base de indicadores

In [14]:
#Selecionando variáveis para cálculo de indicadores no survey
pns2019Osurvey<- pns2019.1 %>% select("V0024","UPA_PNS","peso_morador_selec", "O002P","O003P","O004P" ,"O005P","O006P","O007P","O008P",
                                     "C008","C009","V0031","Sit_Urbano_Rural","Sexo","Unidades_da_Federacao", "GrandesRegioes",
                                     "faixa_idade", "Raca","rend_per_capita","gescol","Capital")
summary(pns2019Osurvey)

     V0024            UPA_PNS      peso_morador_selec  O002P        O003P      
 1210010: 1167   140001681:   18   Min.   : 0.00582   Sim :45832   Sim :17149  
 1410011:  792   140003815:   18   1st Qu.: 0.27579   Não :38603   Não : 5254  
 2710111:  779   140005777:   18   Median : 0.56358   NA's: 6411   NA's:68443  
 2410011:  745   140006746:   18   Mean   : 1.03597                            
 5010011:  738   140007081:   18   3rd Qu.: 1.16822                            
 3210011:  711   140007715:   18   Max.   :63.29775                            
 (Other):85914   (Other)  :90738                                               
  O004P        O005P       O006P        O007P       O008P      
 Sim :40636   Sim :11479   Sim: 2257   Sim :26396   Sim:68537  
 Não :15126   Não :30406   Não:88589   Não : 4973   Não:22309  
 NA's:35084   NA's:48961               NA's:59477              
                                                               
                                        

In [15]:
#Salvando csv para cálculo de indicadores no survey
path <- "../dados"
write.csv(pns2019Osurvey, file.path(path, "pns2019Osurvey.csv"))

### Cria plano amostral complexo

In [16]:
desPNSO=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, data=pns2019Osurvey)

In [17]:
#survey design -O006P e O008P
desPNSO_18=subset(desPNSO, C008>=18)
desPNSO_R18=subset(desPNSO, C008>=18 & !is.na(Raca))
desPNSO_C18=subset(desPNSO, C008>=18 & V0031==1)

In [18]:
#survey design -O002P
desPNSO002P_18=subset(desPNSO, C008>=18 & !is.na(O002P))
desPNSO002P_C18=subset(desPNSO, C008>=18 & V0031==1 & !is.na(O002P))
desPNSO002P_R18=subset(desPNSO, C008>=18 & !is.na(Raca) & !is.na(O002P))

In [19]:
#survey design -O003P
desPNSO003P_18=subset(desPNSO, C008>=18 & !is.na(O003P))
desPNSO003P_C18=subset(desPNSO, C008>=18 & V0031==1 & !is.na(O003P))
desPNSO003P_R18=subset(desPNSO, C008>=18 & !is.na(Raca) & !is.na(O003P))

In [20]:
#survey design -O004P
desPNSO004P_18=subset(desPNSO, C008>=18 & !is.na(O004P))
desPNSO004P_C18=subset(desPNSO, C008>=18 & V0031==1 & !is.na(O004P))
desPNSO004P_R18=subset(desPNSO, C008>=18 & !is.na(Raca) & !is.na(O004P))

In [21]:
#survey design -O005P
desPNSO005P_18=subset(desPNSO, C008>=18 & !is.na(O005P))
desPNSO005P_C18=subset(desPNSO, C008>=18 & V0031==1 & !is.na(O005P))
desPNSO005P_R18=subset(desPNSO, C008>=18 & !is.na(Raca) & !is.na(O005P))

In [22]:
#survey design -O007P
desPNSO007P_18=subset(desPNSO, C008>=18)
desPNSO007P_R18=subset(desPNSO, C008>=18 & !is.na(Raca))
desPNSO007P_C18=subset(desPNSO, C008>=18 & V0031==1)

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [23]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [24]:
ListaIndicadores = c(~O002P,~O003P,~O004P,~O005P,~O006P,~O007P,~O008P)
ListaIndicadoresTexto = c("O002P","O003P","O004P","O005P","O006P","O007P","O008P")
ListaDominios = c(~Sexo,~Raca,~rend_per_capita,~faixa_idade,~Sit_Urbano_Rural,~Unidades_da_Federacao,~GrandesRegioes,~gescol,~Capital)
ListaDominiosTexto = c("sexo","raça","rend_per_capita","fx_idade_acid","urb_rur","uf","região","gescol","capital")
ListaTotais = c('Brasil','Capital')
Ano <- "2019"

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [25]:
#Cálculo dos indicadores usando o pacote survey 
i <- 0
#Para cada indicador
for( indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
    #Para cada dominio
    for (dominio in ListaDominios){
               #design especifico para capital que é subconjunto do dataframe total
               if (ListaDominiosTexto[j]=="capital"){
                   #designs especificos por variavel que são subconjuntos do dataset total
                   if(ListaIndicadoresTexto[i] == "O002P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO002P_C18 , svymean,vartype= c("ci", "cv"))
                   }else if(ListaIndicadoresTexto[i] == "O003P"){# cv maior do que o aceitável
                     next
                   }else if(ListaIndicadoresTexto[i] == "O004P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO004P_C18 , svymean,vartype= c("ci", "cv"))
                   }else if(ListaIndicadoresTexto[i] == "O005P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO005P_C18 , svymean,vartype= c("ci", "cv"))
                   }else {
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO_C18 , svymean,vartype= c("ci", "cv"))
                   }
               #Uso design do subconjunto para raça/cor que inclui preta,branca e parda as outras 
               #não possuiam dados suficientes para os dominios dos indicadores
               }else if (ListaDominiosTexto[j]=="raça"){
                   if(ListaIndicadoresTexto[i] == "O002P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO002P_R18 , svymean,vartype= c("ci", "cv"))
                   }else if(ListaIndicadoresTexto[i] == "O003P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO003P_R18 , svymean,vartype= c("ci", "cv"))
                   }else if(ListaIndicadoresTexto[i] == "O004P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO004P_R18 , svymean,vartype= c("ci", "cv"))
                   }else if(ListaIndicadoresTexto[i] == "O005P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO005P_R18 , svymean,vartype= c("ci", "cv"))
                   }else {
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO_R18 , svymean,vartype= c("ci", "cv"))
                   }
               #design geral para o subconjunto maior que 18 anos
               }else {
                   if(ListaIndicadoresTexto[i] == "O002P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO002P_18 , svymean,vartype= c("ci", "cv"))
                   }else if(ListaIndicadoresTexto[i] == "O003P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO003P_18 , svymean,vartype= c("ci", "cv"))
                   }else if(ListaIndicadoresTexto[i] == "O004P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO004P_18 , svymean,vartype= c("ci", "cv"))
                   }else if(ListaIndicadoresTexto[i] == "O005P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO005P_18 , svymean,vartype= c("ci", "cv"))
                   }else {
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO_18 , svymean,vartype= c("ci", "cv"))
                   }
               }
               #União do dataframe de indicadores no formato do painel disponibilizado para PNS
               
               dataframe_indicador<-data.frame(dataframe_indicador)
               
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
    }
}

#### Criando a tabela pela abrangência total

In [26]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [ ]:
i=0
#para cada indicador
for(indicador in ListaIndicadores){
    i <- i+1
    #para os totais Brasil e total das capitais
    for(total in ListaTotais){
        #Uso do design que é subconjunto do dataset para cada Capital
        if (total == "Capital"){
                   #Indicadores que são subconjunto do dataset tot
                   if(ListaIndicadoresTexto[i] == "O002P"){
                           dataframe_indicador <- svymean(indicador,desPNSO002P_C18)
                   }else if(ListaIndicadoresTexto[i] == "O003P"){
                           dataframe_indicador <- svymean(indicador,desPNSO003P_C18)
                   }else if(ListaIndicadoresTexto[i] == "O004P"){
                           dataframe_indicador <- svymean(indicador,desPNSO004P_C18)
                   }else if(ListaIndicadoresTexto[i] == "O005P"){
                           dataframe_indicador <- svymean(indicador,desPNSO005P_C18)
                   }else {
                           dataframe_indicador <- svymean(indicador,desPNSO_C18)
                   }
                   
        } else {
                   if(ListaIndicadoresTexto[i] == "O002P"){
                           dataframe_indicador <- svymean(indicador,desPNSO002P_18)
                   }else if(ListaIndicadoresTexto[i] == "O003P"){
                           dataframe_indicador <- svymean(indicador,desPNSO003P_18)
                   }else if(ListaIndicadoresTexto[i] == "O004P"){
                           dataframe_indicador <- svymean(indicador,desPNSO004P_18)
                   }else if(ListaIndicadoresTexto[i] == "O005P"){
                           dataframe_indicador <- svymean(indicador,desPNSO005P_18)
                   }else {
                           dataframe_indicador <- svymean(indicador,desPNSO_18)
                   }
                }
      
        intervalo_confianca <- confint(dataframe_indicador)
        coeficiente_variacao <- cv(dataframe_indicador)
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))
        
        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        dataframe_indicador_S <- dataframe_indicador %>% 
                                 slice(1)
                
        colnames(dataframe_indicador_S) <- c('Sim','LowerS','UpperS', 'cvS')
        dataframe_indicador_S$Indicador <- ListaIndicadoresTexto[i]
        print(ListaIndicadoresTexto[i])
        dataframe_indicador_S$abr_tipo <- "total"
        dataframe_indicador_S$abr_nome <- total
        dataframe_indicador_S$Ano <- Ano 
        print(colnames(dataframe_indicador_S))
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS",'cvS')
        
        matriz_totais <-rbind(matriz_totais,dataframe_indicador_S)
        
    }
}

#### Unindo tabela de indicadores e de totais

In [44]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Exportando tabela de indicadores

In [46]:
write.table(matrizIndicadores,file="<coloque aqui o caminho para exportação da matriz de indicadores>",sep = ";",dec = ",",row.names = FALSE)